In [1]:
cd ..

C:\Users\wpgur\OneDrive\프로그래밍\Back-End\tdatlib


In [2]:
from IPython.display import display, HTML
display(HTML("<style>.container { width:80% !important;}</style>"))

import plotly.graph_objects as go
import pandas as pd
import numpy as np
from plotly.subplots import make_subplots
from tqdm.notebook import tqdm
from snob import tools, ecos, fred, krse, idex, kr

# The Basics

(Thumbnail)

<b>요약</b>
* '80년대 John Bollinger에 의해 개발
* 중심선과 상/하 가격 밴드로 구성
* 중심선은 단순 이동 평균(SMA)으로 계산되며 상/하 밴드는 대상 증권의 표준 편차로 계산
* 밴드는 가격 변동이 클 때 팽창하고 작을 때 수축
* 상/하 밴드를 목표가로 트레이딩하기 위한 목적으로 개발

볼린저 밴드는 미국의 재무 분석가 존 볼린저(John A. Bollinger, 1950.5.27~)에 의해 개발된 유가 증권의 기술적 분석 도구입니다. 정의는 꽤 단순합니다. 주가의 이동평균선을 중심선으로 하고 가격의 변동성을 나타내는 이동표준편차를 상/하단에 일정 거리만큼 두어 위치 시키면 끝입니다. 이 때 이동평균선 및 이동표준편차는 일반적으로 20거래일을 기준으로 하고 두 지표간 거리는 2배수만큼 차이 나게 위치시키는 것이 일반적입니다.

> $(중심선; Center Line) = (종가 또는 Typical Price)의 20거래일 평균값$
$(상단선; Upper Line) = 중심선 + 2 x (종가 또는 Typical Price)의 20거래일 표준편차값$
$(하단선; Lower Line) = 중심선 - 2 x (종가 또는 Typical Price)의 20거래일 표준편차값$

이 때, Typical Price는 (종가 + 고가 + 저가) / 3으로 정의합니다.

## 개발 배경

In [ ]:
idex.period = 5
kospi = idex.kospi
kospi_bb = tools.bollinger_band(ohlcv=kospi, name='코스피')

fig = kospi_bb.figure_basic
fig['data'][3]['yhoverformat'] = ',d'
fig.update_layout(
    margin=dict(r=1),
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    )
)
fig.show()

볼린저 밴드는 직관적으로 지지/저항, 다시 말해 목표하는 매매 가격의 상한선과 하한선을 찾을 수 있도록 돕습니다.
경우에 따라서는 중심선이 지지/저항선의 역할을 할 수도 있죠.
그래서 이 지표의 개발 초기에는 하한선에 도달했을 때 매수, 상한선에 도달했을 때 매도하는 기법이 각광 받기도 했습니다.

## 한계점

물론 현재 이 방식으로 투자를 하는 것은 권하지 않는 위험한 방법입니다.
상승 또는 하락 추세에 있는 주식의 경우 지속적으로 상한선 또는 하한선을 타고 이동하며 변동성을 키우기도 하기 때문입니다.
무턱대고 주가가 밴드 하한선에 도달했다고 매수를 했다가는 큰 손실을 볼 수도 있습니다.
상기 사례에서 볼 수 있듯이 볼린저 밴드는 단독 사용 시 오인 신호(Fault Signal)을 만들 수 있습니다.
따라서 볼린저 밴드는 다른 지표들과 함께 보조 지표로 사용해야 하는 점을 꼭 유의해야합니다.

In [ ]:
skhynix = kr('000660')
skhynix.period = 5

skhynix_bb = tools.bollinger_band(ohlcv=skhynix.ohlcv, name='SK하이닉스', unit='KRW')
fig = skhynix_bb.figure_basic
fig['data'][3]['yhoverformat'] = ',d'
fig.update_layout(
    margin=dict(r=0),
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    )
)
fig.show()

## 변동성 지표: 밴드 폭

(밴드 폭; Width) = 

밴드의 폭은 이동표준편차, 즉 누적된 변동성을 나타냅니다. 밴드의 폭이 넓어진다는 말은 곧 주가의 변동성이 커진다는 말과 같습니다.
변동성은 다른 말로 리스크입니다. 높은 리스크에는 높은 수익률이 따라올 수도 있고, 처참한 수익률이 기다리고 있을 수도 있습니다.
따라서 변동성 지표를 활용한다면 적절한 리스크 관리를 할 수 있겠죠.

In [ ]:
kb = kr('105560')
kb.period = 5

kb_bb = tools.bollinger_band(ohlcv=kb.ohlcv, name='KB금융', unit='KRW')
fig = make_subplots(rows=3, cols=1, shared_xaxes=True, row_width=[0.3, 0.15, 0.55], vertical_spacing=0.01)

fig.add_trace(kb_bb.trace_upper_edge, row=1, col=1)

trace_middle = kb_bb.trace_middle
trace_middle.line = dict(color='rgb(197, 224, 180)')
fig.add_trace(trace_middle, row=1, col=1)

trace_lower = kb_bb.trace_lower_edge
trace_lower.line = dict(color='rgb(197, 224, 180)')
fig.add_trace(trace_lower, row=1, col=1)

trace_price = tools.draw_candle(data=kb.ohlcv, name='KB금융')
fig.add_trace(trace_price, row=1, col=1)

trace_volume = tools.draw_bar(data=kb.ohlcv.거래량, name="거래량")
trace_volume.marker = dict(color=kb.ohlcv.거래량.pct_change().apply(lambda x: 'blue' if x < 0 else 'red'))
fig.add_trace(trace_volume, row=2, col=1)

fig.add_trace(kb_bb.trace_width, row=3, col=1)

fig.update_layout(
    title=f"볼린저밴드와 변동성: {kb_bb.name}", plot_bgcolor="white", height=750,
    margin=dict(r=0),
    legend=dict(
        tracegroupgap=5,
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    ),
    xaxis=dict(
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=1, linecolor='grey', mirror=False
    ),
    yaxis=dict(
        title=f"{kb_bb.name}[{'-' if not kb_bb.curr else kb_bb.curr}]",
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=0.5, linecolor='grey', mirror=False
    ),
    xaxis2=dict(
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=1, linecolor='grey', mirror=False
    ),
    yaxis2=dict(
        title=f"거래량",
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=0.5, linecolor='grey', mirror=False
    ),
    xaxis3=dict(
        showticklabels=True, tickformat='%Y/%m/%d',
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=1, linecolor='grey', mirror=False
    ),
    yaxis3=dict(
        title=f"밴드 폭[%]",
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=0.5, linecolor='grey', mirror=False
    ),
    xaxis_rangeslider=dict(visible=False),
    xaxis_rangeselector=dict(
        buttons=list([
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=3, label="3m", step="month", stepmode="backward"),
            dict(count=6, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(step="all")
        ])
    ),
)

## %B: 과매수/과매도 판단 지표


(밴드 대비 가격; %B) = 

일반적으로 가격이 상한성을 상회한다면 과매수(Over-Bought) 상태라고 합니다. 주가가 과열되었다는 것이죠. 이 경우는 확률적으로 주가가 하락할 가능성이 높다고 판단합니다.
반대로 가격이 하한선을 하회한다면 과매도(Over-Sold) 상태라고 합니다. 주가가 필요 이상으로 하락했다고 판단하며 주가의 상승 여력이 있는 가능성을 엿볼 수 있습니다.


이 외에도 볼린저 밴드를 활용한 다양한 투자 기법이 있습니다. 이어지는 칼럼에서 확인하세요!

In [ ]:
hyundai = kr('035420')
hyundai.period = 5

hyundai_bb = tools.bollinger_band(ohlcv=hyundai.ohlcv, name='NAVER', unit='KRW')

fig = make_subplots(rows=3, cols=1, shared_xaxes=True, row_width=[0.3, 0.15, 0.55], vertical_spacing=0.01)

fig.add_trace(hyundai_bb.trace_upper_edge, row=1, col=1)

trace_middle = hyundai_bb.trace_middle
trace_middle.line = dict(color='rgb(197, 224, 180)')
fig.add_trace(trace_middle, row=1, col=1)

trace_lower = hyundai_bb.trace_lower_edge
trace_lower.line = dict(color='rgb(197, 224, 180)')
fig.add_trace(trace_lower, row=1, col=1)

trace_price = tools.draw_candle(data=hyundai_bb.ohlcv, name=hyundai_bb.name)
fig.add_trace(trace_price, row=1, col=1)

trace_volume = tools.draw_bar(data=hyundai_bb.ohlcv.거래량, name="거래량")
trace_volume.marker = dict(color=hyundai_bb.ohlcv.거래량.pct_change().apply(lambda x: 'blue' if x < 0 else 'red'))
fig.add_trace(trace_volume, row=2, col=1)

fig.add_trace(hyundai_bb.trace_pctb, row=3, col=1)
fig.add_hrect(y0=1, y1=hyundai_bb.pctb.max(), line_width=0, fillcolor='red', opacity=0.2, row=3, col=1)
fig.add_hrect(y0=hyundai_bb.pctb.min(), y1=0, line_width=0, fillcolor='green', opacity=0.2, row=3, col=1)

fig.update_layout(
    title=f"볼린저밴드와 상대 매수 지표: {hyundai_bb.name}", plot_bgcolor="white", height=750,
    margin=dict(r=0),
    legend=dict(
        tracegroupgap=5,
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    ),
    xaxis=dict(
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=1, linecolor='grey', mirror=False
    ),
    yaxis=dict(
        title=f"{hyundai_bb.name}[{'-' if not hyundai_bb.curr else hyundai_bb.curr}]",
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=0.5, linecolor='grey', mirror=False
    ),
    xaxis2=dict(
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=1, linecolor='grey', mirror=False
    ),
    yaxis2=dict(
        title=f"거래량",
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=0.5, linecolor='grey', mirror=False
    ),
    xaxis3=dict(
        showticklabels=True, tickformat='%Y/%m/%d',
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=1, linecolor='grey', mirror=False
    ),
    yaxis3=dict(
        title=f"%B[-]",
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=0.5, linecolor='grey', mirror=False
    ),
    xaxis_rangeslider=dict(visible=False),
    xaxis_rangeselector=dict(
        buttons=list([
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=3, label="3m", step="month", stepmode="backward"),
            dict(count=6, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(step="all")
        ])
    ),
)
fig.show()

재차 강조하지만 보조 지표는 투자를 돕는 분석 도구이지 선행 지표가 아닙니다. 이는 결코 완벽하지 않으며 여기에 대한 과한 의존성은 건강한 투자를 해치는 요인이 됩니다.
하지만 적절한 가설과 검증을 통해 만들어진 기법은 빠른 투자 의사결정에 도움이 될 수 있습니다.
[Snowballing]에서는 투자에 유익한 정보를 보다 안전하고 신뢰성있게 다루기 위해 노력하겠습니다. 

# Back-Test

In [3]:
basis = krse.wi26.join(krse.overview.drop(columns=['종목명']))
basis = basis.sort_values(by='시가총액', ascending=False)
basis

종목명      섹터        IPO      종가             시가총액       거래량  \
종목코드                                                                       
005930        삼성전자     반도체 1975-06-11   63400  377887235415000  16783493   
373220    LG에너지솔루션    IT가전 2022-01-27  484000  113022000000000    365266   
000660      SK하이닉스     반도체 1996-12-26   91400   66466615924500   3606882   
207940    삼성바이오로직스    건강관리 2016-11-10  798000   56725678000000     35890   
051910        LG화학      화학 2001-04-25  652000   46096799979000    220889   
...            ...     ...        ...     ...              ...       ...   
054220       비츠로시스   소프트웨어 2001-12-26     854      21463939199    150982   
064090     에프앤리퍼블릭  소매(유통) 2002-12-17    1513      20718088454    462928   
044180          KD      건설 2000-11-16     758      18835269878     18636   
161570  THE MIDONG     자동차 2013-11-13    1202      18652647510    337092   
174880        장원테크  IT하드웨어 2016-07-15     799      17459341025    294252   

                 거래대금       상장주식수       BPS     PER    PBR      EPS   DIV  \
종목코드                                                                        
005930  1063717604600  5969782550   43611.0   10.97   1.45   5777.0  2.28   
373220   175078514500   234000000   39831.0  122.13  12.15   3963.0  0.00   
000660   329587423200   728002365   90394.0    6.53   1.01  13989.0  1.68   
207940    28712278000    71174000   74551.0  135.74  10.70   5879.0  0.00   
051910   143394025000    70592343  278455.0   13.84   2.34  47108.0  1.84   
...               ...         ...       ...     ...    ...      ...   ...   
054220      129010021    25162883     559.0    3.92   1.53    218.0  0.00   
064090      710062254    13576729    1169.0   19.65   1.29     77.0  0.00   
044180       14116986    24848641    1578.0    0.00   0.48      0.0  0.00   
161570      411238179    15582830    1194.0    0.00   1.01      0.0  0.00   
174880      234176121    21906325    4845.0    0.00   0.16      0.0  0.00   

            DPS  
종목코드             
005930   1444.0  
373220      0.0  
000660   1540.0  
207940      0.0  
051910  12000.0  
...         ...  
054220      0.0  
064090      0.0  
044180      0.0  
161570      0.0  
174880      0.0  

[2257 rows x 14 columns]

## Stochastic Strategy

### Singular

In [4]:
fetch = kr('012330', basis)

stock = tools.bollinger_band(ohlcv=fetch.ohlcv, name=fetch.name, unit=fetch.curr)
est = tools.evaluate(stock.ohlcv, stock.obos_signal, fetch.name)
# est.edges
est.eval()

TRADING DAYS  BUY SIGNALED  OVER PERFORM  SUCCESS RATE  AVERAGE RISE  \
현대모비스          4943           112            79         70.54          9.73   

       AVERAGE DROP  BEST CASE BEST CASE DATE  WORST CASE WORST CASE DATE  
현대모비스          -6.0      41.54     2020-03-20       -41.8      2020-02-26

In [6]:
fig = stock.figure_full



fig.update_layout(
    title=f"볼린저밴드 스토캐스틱 전략: {fetch.name}({fetch.ticker})", plot_bgcolor="white", height=750,
    margin=dict(r=0),
    legend=dict(
        tracegroupgap=5,
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    ),
)
fig.show()

### Plural :: Large Cap.

In [ ]:
fetches = dict()
ests = list()

loop = tqdm(basis.head(100).index)
for ticker in loop:
    name = basis.loc[ticker, '종목명']
    loop.set_description(desc=f'{name}({ticker})')
    f = kr(ticker)
    fetches[ticker] = tools.bollinger_band(ohlcv=f.ohlcv, name=name, unit=f.curr)
    est = tools.evaluate(f.ohlcv, fetches[ticker].obos_signal, name)
    ests.append(est.eval())

estimated = pd.concat(ests, axis=0)
estimated

In [ ]:
estimated['SUCCESS RATE'].mean()